In [1]:
from bs4 import BeautifulSoup
import re
import requests
import pandas
import pandas as pd
sample="""
<div class="textlist"> <a href="http://finance.jxufe.edu.cn/news-show-1347.html">曹邓</a></div>
"""

url1="http://finance.jxufe.edu.cn/news-list-shuodao.html"#第一页
url2="http://finance.jxufe.edu.cn/news-list-shuodao-2.html"#第二页
url3="http://finance.jxufe.edu.cn/news-list-shuodao-3.html"#第三页

In [3]:
#做一个循环的正则查找
def get_teachers_href(url):
    r=requests.get(url)
    html_text=r.text
    searchObj_s=re.findall(r'<div class="textlist">.*?</div>',html_text)
    links_teacher={}
    for item in searchObj_s:
        name=item[81:-10]
        name=name.replace(' ','')#删除空格
        href=item[32:79]
        links_teacher[name]=href
    return(links_teacher)
links1=get_teachers_href(url1)
links2=get_teachers_href(url2)
links3=get_teachers_href(url3)#将不同网页依次排列，并得到每个网页的硕导
links={}#三个字典合并成一个
links.update(links1)
links.update(links2)
links.update(links3)
herfs=list(links.values())


In [4]:
herfs

['http://finance.jxufe.edu.cn/news-show-3097.html',
 'http://finance.jxufe.edu.cn/news-show-1347.html',
 'http://finance.jxufe.edu.cn/news-show-1348.html',
 'http://finance.jxufe.edu.cn/news-show-1349.html',
 'http://finance.jxufe.edu.cn/news-show-2066.html',
 'http://finance.jxufe.edu.cn/news-show-1346.html',
 'http://finance.jxufe.edu.cn/news-show-1343.html',
 'http://finance.jxufe.edu.cn/news-show-1345.html',
 'http://finance.jxufe.edu.cn/news-show-1344.html',
 'http://finance.jxufe.edu.cn/news-show-3085.html',
 'http://finance.jxufe.edu.cn/news-show-1342.html',
 'http://finance.jxufe.edu.cn/news-show-1341.html',
 'http://finance.jxufe.edu.cn/news-show-1337.html',
 'http://finance.jxufe.edu.cn/news-show-1312.html',
 'http://finance.jxufe.edu.cn/news-show-1376.html',
 'http://finance.jxufe.edu.cn/news-show-1335.html',
 'http://finance.jxufe.edu.cn/news-show-2751.html',
 'http://finance.jxufe.edu.cn/news-show-2063.html',
 'http://finance.jxufe.edu.cn/news-show-1332.html',
 'http://fin

In [5]:
def get_value(key,html):
    pattern='%s</strong>.*?：(.*?)(</p>|<img)'%key
    searchObj=re.search(pattern,html)
    value=searchObj.group(1)
    return(value)

def get_zwjj(key,html):
    zwjj = re.findall(r'自我简介(.*?)科研成果', html)
    zwjj_text = re.sub(r'</p>','\n',zwjj[0])
    zwjj_text_clear = re.sub(r'<(.*?)>','', zwjj_text).replace("&nbsp;","").replace("\n"," ").strip()
    return zwjj_text_clear 

def get_kycg(key,html):
    kycg = re.findall(r'<span.*?科研成果(.*?)版权所有',html,re.S)
    kycg_text = re.sub(r'</p>','\n',kycg[0])
    kycg_text_clear = re.sub(r'<(.*?)>','', kycg_text).replace("&nbsp;","").replace("\n"," ").strip("：").strip()
    return kycg_text_clear    



In [6]:
def parse_content(html):
    xm=get_value('姓　　名',html)
    xb=get_value('性　　别',html)
    zzmm=get_value('政治面貌',html)
    byyx=get_value('毕业院校',html)
    byzy=get_value('毕业专业',html)
    zw=get_value('职　　务',html)
    zc=get_value('职　　称',html)
    zwjj = get_zwjj('自我简介',html)
    kycg = get_kycg('科研成果',html)
    teacher_info={'姓名':xm,
                  '性别':xb,
                  '政治面貌':zzmm,
                  '毕业院校':byyx,
                  '毕业专业':byzy,
                  '职务':zw,
                  '职称':zc,
                  '自我简介':zwjj,
                  '科研成果':kycg}
    return(teacher_info)

In [7]:
tol_list = []
def fail_list(herfs):
    fail_list = []
    for i in range(len(herfs)):
        t = requests.get(herfs[i]).text
        try:
            parse_content(t)
            a = parse_content(t)
            tol_list.append(a)
        except:
           fail_list.append(i)
    return fail_list 
fail_list(herfs)
tol_list

df =  pd.DataFrame.from_dict(tol_list)


In [8]:
#打印符合模板的老师信息
df

姓名 性别  政治面貌          毕业专业      毕业院校  \
0    曹邓  女  中共党员           管理学    江西财经大学   
1   陈春霞  女    群众           金融学    江西财经大学   
2   陈家洪  男  中共党员  经济统计（证券研究方向）    江西财经大学   
3   冯凌秉  男                 统计学  澳大利亚国立大学   
4   胡少勇  男  中共党员           精算学    华东师范大学   
5   胡援成  男    党员           金融学      厦门大学   
6   胡志军  男  中共党员         数量经济学    上海财经大学   
7   李思敏  男  中共党员                           
8   刘金凤  女                                 
9   刘兴华  男  中共党员          世界经济      厦门大学   
10  吕江林  男  中共党员           经济学    中南财经大学   
11  钱建豪  男               经济学博士             
12   寿晖  男                                 
13  孙爱琳  女  中共党员         政治经济学      浙江大学   
14   汪洋  男  中共党员           金融学    上海财经大学   
15   王辉  男  中共党员           财政学    江西财经大学   
16  王清生  男    群众      概率论与数理统计      云南大学   
17  吴伟军  男  中共党员           经济学    江西财经大学   
18   严武  男    党员           经济学    江西财经大学   
19   杨荣  女  中共党员           金融学    江西财经大学   
20  杨玉凤  女  民主党派           金融学    江西财经大学   
21  邹朋飞  男    群众           金融学      暨南大学   
22  曾鸿志  男    党员       投资经济管理学      天津大学   

                                                 科研成果  \
0   一、论文1.“WTO:中国民族保险业的机遇与挑战”，独著，《理论导报》2000年第9期。2....   
1   一、论文1、《我国国债与企业债券的比较》，独著，《江西财经大学学报》2006年第9月期（人大...   
2   一、论文1. “从股票市场角度看收入分配不公问题”，独著，《华东经济管理》2011年第8期。...   
3   Published Papers： L. Feng, Gen. Nowak, T. J. O...   
4   科研成果 五、发表的主要论文： 1. Shaoyong Hu,Ailin Zhu,2016....   
5   一、论文1、“地价模型初探”，独著，数量经济与技术经济研究 1990年第6期。2、“商业银行...   
6   论文： [16]Hu Z, Sun P-W. Connectedness among sto...   
7                                                       
8                                                       
9   一、论文1.“欧债危机的救援困境及其对欧元区的影响”，独著，《国际论坛》2012年第4期。2...   
10  主要科研成果一、论文1、《具有联合椭圆不确定集与概率约束的鲁棒投资组合选择》，《控制与决策》...   
11                                                      
12                                                      
13  一、论文 1.“完善我国国家公务员养老保险制度的思考”，独著，《江西财经大学学报》2001年...   
14  发表的主要论文：1.    《跨境贸易以人民币结算：路径选择与风险》，《国际经济评论》，独著...   
15  一、论文 1.“加快建立有中国特色的社会保障法律体系”，独著，《财经论丛》2000年第3期。...   
16  主要研究方向为非线性金融时间序列建模、证券投资策略、金融风险管理；先后在国内刊物上公开发表学...   
17  一、学术论文 [1]吴伟军，转轨时期中国货币政策传导机制有效性的实证研究, [J]《江西社会...   
18  主要成果：  （一）论文论著 1. 中国股市周期的划分与实证分析：1991-2004（第一作...   
19  一、论文 2000年以来论文 1、影响我国企业集团形成与健康发展原因剖析 《国民经济运行与调...   
20  一、论文 1.“加快表外业务的发展和创新”，独著，《金融与经济》2002年第3期。 2.“从...   
21  发表的主要论文： 1.银行信贷、房地产价格与实际产出关系的经验研究,独著,2008-12,山...   
22  一、论文  1．曾鸿志，货币调整、资本市场与实体部门的长期互动,《中国经济问题》，2011（...   

                                                   职务      职称  \
0                                                          教授   
1                                                       教授/硕导   
2                                                       教授/硕导   
3                                                        助理教授   
4                                                 副院长     副教授   
5                                                中心主任   教授/博导   
6                                                         副教授   
7                                                 系主任     副教授   
8                                                               
9                                                 副院长   教授/博导   
10                                         应用金融研究中心主任   教授/博导   
11                                          高等教育研究所所长    副研究员   
12                                                              
13                                                      教授、硕导   
14                                                      教授/博导   
15                                                      教授/硕导   
16                                                         讲师   
17  <span style="color:#343434;font-family:微软雅黑, &...     副教授   
18                                                         教授   
19                                                      教授、硕导   
20                                                      教授/硕导   
21                                           货币银行系副主任  副教授/硕导   
22                                                        副教授   

                  

In [9]:
#查找有邮箱的硕导以及其邮箱信息

In [10]:
def parse_content1(html):
    xm=get_value('姓　　名',html)
    yx=get_value('邮&nbsp; &nbsp; &nbsp; &nbsp;箱',html)
    teacher1_info={'姓名':xm,
                  '邮箱':yx,
                           }
    return(teacher1_info)
total_list = []
def fails_list(herfs):
    fails_list = []
    for i in range(len(herfs)):
        t = requests.get(herfs[i]).text
        try:
            parse_content1(t)
            a = parse_content1(t)
            total_list.append(a)
        except:
           fails_list.append(i)
    return fails_list 
fails_list(herfs)
total_list    
df1 =  pd.DataFrame.from_dict(total_list) 

In [11]:
df1

姓名                                                 邮箱
0    曹邓                               laotoutou@aliyun.com
1   陈春霞                                    new9360@163.com
2   陈家洪                                     jxmcjh@126.com
3   桂荷发                                    guihefa@163.com
4   胡少勇                                    45022251@qq.com
5   李思敏                               jxcdzqtzxlsm@126.com
6   刘兴华                                    lxh7572@126.com
7   吕江林                                    ljl5983@126.com
8    寿晖                                13970014516@163.com
9   孙爱琳                                    sal6660@126.com
10   汪洋                              wangyang@jxufe.edu.cn
11   王辉  “保险学”；“人身保险”；“责任保险”；“保险经营管理”；“保险营销学”；“风险管理”；“证...
12  王清生                           ynuwangqingsheng@163.com
13  吴伟军                                    wwj1277@163.com
14   杨荣                               yonghongyang@163.com
15  杨玉凤                                  xialuoren@126.com
16  邹朋飞                                 Pengfeizou@163.com
17  曾鸿志                                    18409495@qq.com

In [9]:
#硕导Badar Nadeem Ashraf
teacher2 = {}
teacher2['Name'] = 'Badar Nadeem Ashraf'
teacher2['Sex'] = 'Male'
teacher2['Job title'] = 'Associate Professor'
teacher2['Graduated'] = 'Huazhong University of Science and Technology'
teacher2['Duties'] = 'Teaching/Research/Research supervision'
teacher2['Email'] = 'badar@jxufe.edu.cn'
shuo_dao = []
shuo_dao.append(teacher2)

url="http://finance.jxufe.edu.cn/news-show-3097.html"
html=requests.get(url)
text=html.text
#学历
start_index=text.find('1.Education')
end_index=text.find('2.Research Interests')
educ=text[start_index:end_index]
def clear_tags(html_text):
    p=re.compile('<.*?>')
    text=''
    remaining_text=html_text
    searchObj=p.search(remaining_text)
    while searchObj is not None:
        text+=remaining_text[:searchObj.start()]
        remaining_text=remaining_text[searchObj.end():]
        searchObj=p.search(remaining_text)
    return(text)        
educ_text=clear_tags(educ)
    
#研究兴趣
start_index=text.find('2.Research Interests')
end_index=text.find('3.Major Research Publications')
reser=text[start_index:end_index]
def clear_tags(html_text):
    p=re.compile('<.*?>')
    text=''
    remaining_text=html_text
    searchObj=p.search(remaining_text)
    while searchObj is not None:
        text+=remaining_text[:searchObj.start()]
        remaining_text=remaining_text[searchObj.end():]
        searchObj=p.search(remaining_text)
    return(text)     
reser_text=clear_tags(reser)

#论文
start_index=text.find('3.Major Research Publications')
end_index=text.find('4.Awards')
public=text[start_index:end_index]
def clear_tags(html_text):
    p=re.compile('<.*?>')
    text=''
    remaining_text=html_text
    searchObj=p.search(remaining_text)
    while searchObj is not None:
        text+=remaining_text[:searchObj.start()]
        remaining_text=remaining_text[searchObj.end():]
        searchObj=p.search(remaining_text)
    return(text)     
public_text=clear_tags(public)

#奖项
start_index=text.find('4.Awards')
end_index=text.find('版权所有')
awa=text[start_index:end_index]
def clear_tags(html_text):
    p=re.compile('<.*?>')
    text=''
    remaining_text=html_text
    searchObj=p.search(remaining_text)
    while searchObj is not None:
        text+=remaining_text[:searchObj.start()]
        remaining_text=remaining_text[searchObj.end():]
        searchObj=p.search(remaining_text)
    return(text)     
awa_text=clear_tags(awa)

In [10]:
shuo_dao

[{'Name': 'Badar Nadeem Ashraf',
  'Sex': 'Male',
  'Job title': 'Associate Professor',
  'Graduated': 'Huazhong University of Science and Technology',
  'Duties': 'Teaching/Research/Research supervision',
  'Email': 'badar@jxufe.edu.cn'}]

In [11]:
educ_text

'1.Education[4] 2012.09-2015.06, Doctor in Business Administration (Accounting &amp; Finance), Huazhong University of Science and Technology, Wuhan, China[3] 2010.09-2012.06, Master in Economics, University of the Punjab, Lahore, Pakistan[2] 2007.01-2010.06, CMA, Institute of Cost &amp; Management Accountants of Pakistan, Islamabad, Pakistan[1] 2003.09-2005.06. Bachelor of Arts, University of the Punjab, Lahore, Pakistan'

In [13]:
reser_text

'2.Research InterestsCryptocurrencies; blockchain technology; Economic policy uncertainty;Banking; financial institutions; financial regulations; law and finance; culture and finance; politics and finance; Corporate governance; earnings management;&nbsp;&nbsp;'

In [14]:
public_text

'3.Major Research Publications[30] The liquidity of major cryptocurrencies and stock markets: Are they connected? Under review in SSCI journal (with Muhammad Umar, Sultan Sikandar Mirza and Tong Fang Hua)  &nbsp;[29] The impact of board internationalization on accrual-based and real activities-based earnings management: Evidence from China, Under review in SSCI journal (with Mengxuan Liu)&nbsp;[28] Capital regulation, deposit insurance and bank risk-taking behavior: international evidence from normal and crisis periods. Research in International Business and Finance, Under review after 1st revision (with Changjun Zheng, Lai Shaojie and Ningyu Qian) SSCI&nbsp;[27] Economic policy uncertainty and banks’ loan pricing. Journal of Financial Stability, 2019, accepted and in press, (with Yinjie Shen) SSCI &nbsp;[26] How do regulatory ability and bank competition affect the adoption of explicit deposit insurance scheme and banks’ risk-taking behavior? International Review of Economics and Fina

In [15]:
awa_text

'4.Awards[5] “Best Thesis Supervision Award of the Year” from East China Jiao Tong University, China for the academic year 2018-19&nbsp;[4] “Outstanding Reviewer Certificate” from the journal ‘Economic Modelling’ for the year 2016&nbsp;[3] “2016 Emerald Outstanding Paper Literati Award for Excellence” (outstanding paper of the year) for the paper ‘Shareholder protection, creditor rights and bank dividend policies’ published in 2015 in the journal ‘China Finance Review International’&nbsp;[2] “Best Paper Award” from ‘International Conference on Transnational Investment and Trade Relations between USA and Emerging-Market Economies’, 2015, October 29-31, Hubei University, Wuhan, China&nbsp;[1] “Culture-exchange scholarship” of ‘Government of Pakistan’ for PhD 2012&nbsp;&nbsp;                \n      \n    \n     \n  \n\n  \n  \n  \n    \n      \n        \n          \n            '